![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 9,10. <i>Web scraping</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Jak dobrze wiemy, w procesie wspomagania tłumaczenia oraz w zagadnieniach przetwarzania języka naturalnego ogromną rolę pełnią zasoby lingwistyczne. Należą do nich korpusy równoległe (pamięci tłumaczeń), korpusy jednojęzyczne oraz słowniki. Bywa, że zasoby te nie są dostępne dla języka, nad którym chcemy pracować.

W tej sytuacji jest jeszcze dla nas ratunek - możemy skorzystać z zasobów dostępnych publicznie w Internecie. Na dzisiejszych zajęciach przećwiczymy techniki pobierania tekstu ze stron internetowych.

Poniższy kod służy do ściągnięcia zawartości strony (w formacie HTML do zmiennej) oraz do wyszukania na tej stronie konkretnych elementów. Przed jego uruchomieniem należy zainstalować moduł BeautifulSoup:
`pip3 install beautifulsoup4`

In [1]:
import requests
from bs4 import BeautifulSoup

url='https://epoznan.pl'

page = requests.get(url)
soup = BeautifulSoup(page.content, 'html.parser')

headers = soup.find_all('h3', {'class':'postItem__title'})

print('\n'.join([header.get_text() for header in headers]))

W Poznaniu uroczyście odsłonięto monument upamiętniający cmentarz żydowski założony jeszcze w XIX wieku
Przez ulice Poznania przejdzie Marsz dla Życia. Będą utrudnienia
Sierść psa zatopiona w żywicy? Taką biżuterię pamiątkową zlecają właściciele czworonożnych pociech
Nagrał film w jednej z poznańskich "Biedronek". Kilka spleśniałych cytryn w kartonie. "Nikt się tym nie przejmuje"
Gniezno: poszkodowani po ulewie będą mogli ubiegać się o pomoc w ZUS i US. Powstała również specjalna infolinia
Zostawiła jedzenie dla potrzebujących. Coraz więcej głodnych osób, którym nie wystarcza pieniędzy po opłaceniu rachunków
Kolejne ostrzeżenie I stopnia od IMGW. Oprócz burz może wystąpić również grad
Lech przegrał Koroną. Na trybunach marsz żałobny i 'mamy k**** dość'
Warta Poznań po przegranej z Jagielonią Białystok spada do I ligi
Mieszkańcy skarżą się na właściciela samochodu, w którym notorycznie włącza się alarm. "Uprzykrza nam to życie!"
Leśne Placówki Montessori
Na autostradzie samochód wpadł w

### Ćwiczenie 1: Napisz funkcję do pobierania nazw towarów z serwisu Ceneo.pl. Typ towaru, np. telewizor, pralka, laptop jest parametrem funkcji. Wystarczy pobierać dane z pierwszej strony wyników wyszukiwania.

In [10]:
from bs4 import element

def get_names(article_type, page_nr: int = 0):
    url = 'https://www.ceneo.pl/;szukaj-' + article_type + ';0020-30-0-0-' + str(page_nr) + '.htm'
    page = requests.get(url)
    if page_nr != 0 and url != page.url:
        return []
    soup = BeautifulSoup(page.content, 'html.parser')
    result = []

    def is_product_title_container(tag: element.Tag) -> bool:
        if not tag.has_attr('class'):
            return False

        classes = tag.attrs['class']
        if len(classes) != 1:
            return False

        return classes[0] == 'cat-prod-row__name'

    def is_product_title(tag: element.Tag) -> bool:
        if not tag.has_attr('class'):
            return True

        classes = tag.attrs['class']
        if len(classes) != 1:
            return False

        return classes[0] == 'font-bold'

    for tag in soup.find_all(is_product_title_container):
        href = tag.find('a')
        if type(href) is not element.Tag:
            continue
        spans = href.find_all('span')
        for span in spans:
            if is_product_title(span):
                result.append(span.text)

    return result

W ten sposób pobieramy dane z jednej strony. Nic jednak nie stoi nam na przeszkodzie, aby zasymulować przełączanie stron.

### Ćwiczenie 2: Zaobserwuj, jak zmienia się url strony podczas przechodzenia do kolejnych stron wyników wyszukiwania na Ceneo.pl. Wykorzystaj tę informację i uruchom funkcję get_names() na więcej niż jednej stronie wyników.

In [9]:
def scrape_names():
    result = []
    search = 'laptop'
    page = 0
    while True:
        local_result = get_names(search, page)
        if len(local_result) == 0:
            return result
        result = result + local_result
        page += 1

Technika pobierania treści z Internetu jest szczególnie efektywnym sposobem na pozyskiwanie dużych ilości tekstu. Poniższy fragment kodu służy do ściągnięcia całości tekstu ze strony.

In [7]:
import re

url = "https://www.yahoo.com"

page = requests.get(url)
soup = BeautifulSoup(page.content, 'html.parser')

# usunięcie elementów script i style
for script in soup(["script", "style"]):
    script.extract()    # usuń element

# pobierz tekst
text = soup.get_text()

# usuń wielokrotne białe znaki
text = re.sub(r"\s+", " ", text)

print(text)

 Yahoo Make Yahoo Your HomepageDiscover something new every day from News, Sports, Finance, Entertainment and more! HOME MAIL NEWS FINANCE SPORTS ENTERTAINMENT LIFE SHOPPING YAHOO PLUS MORE... Download the Yahoo Home app Yahoo Home Search query Sign in Mail Sign in to view your mail Mail Mail COVID-19 COVID-19 News News Finance Finance Sports Sports Entertainment Entertainment Life Life Shopping Shopping Yahoo Plus Yahoo Plus More... More... Follow live:Closing arguments begin for Derek Chauvin's murder trial in the death of George Floyd 5 people in hospital after shooting in Louisiana One victim was shot in the head, and another suffered multiple gunshot wounds, according to local news outlet.Multiple police units dispatched to scene »2 dead in crash of Tesla with 'no one' drivingMall shooter, 16, faces 1st-degree murder charge'80s pop star rips 'Simpsons' for 'hateful' parodyConspiracy theorist Alex Jones faces a reckoningPig's head left at former home of Chauvin trial witness U.S.Hu

### Ćwiczenie 3: Napisz program do pobrania tekstu ze strony Wydziału Matematyki i Informatyki. Pobierz cały tekst ze strony głównej a następnie wyszukaj na tej stronie wszystkich linków wewnętrznych i pobierz tekst ze stron wskazywanych przez te linki. Nie zagłębiaj się już dalej.


In [8]:
def scrape_wmi():
    def get_text(soup_l: BeautifulSoup) -> str:
        for trash in soup_l(['script', 'style']):
            trash.extract()

        text = soup_l.get_text()

        return re.sub(r'\s+', ' ', text)

    result = []

    base_url = 'https://wmi.amu.edu.pl/'
    page = requests.get(base_url)
    soup = BeautifulSoup(page.content, 'html.parser')
    result.append(get_text(soup))
    for href in soup.find_all('a'):
        if type(href) != element.Tag:
            continue

        if not href.has_attr('href'):
            continue

        if base_url in href.attrs['href']:
            sub_page = requests.get(href.attrs['href'])
            result.append(get_text(BeautifulSoup(sub_page.content, 'html.parser')))


    return result

Omówione wyżej techniki działają również bardzo dobrze dla zasobów słownikowych.

### Ćwiczenie 4: Pobierz jak najwięcej słów w języku albańskim z serwisu glosbe.com.

Nie jest to rozwiązanie zbalansowane, ale pobierze najwięcej słów (Przy odpowiedniej rotacji adresów IP, z których korzystamy, ale założyłem, że kwestia infrastruktury i tego jak strona jest chroniona przed atakami DOS, jest poza zakresem tego zadania)

In [7]:
def scrape_shqip():
    import string

    result = []
    letters = list(string.ascii_lowercase)
    letters_count = len(letters)
    longest_sensible_english_word_len = 28
    base_url = 'https://glosbe.com/en/sq/'

    def get_words(word_l: str) -> list[str]:
        def is_translated_word(tag: element.Tag) -> bool:
            if not tag.has_attr('id') or not tag.has_attr('lang'):
                return False

            if not 'translation__' in tag.attrs['id'] or 'sq' != tag.attrs['lang']:
                return False

            return True

        result_l = []
        page = requests.get(base_url + word_l)
        soup = BeautifulSoup(page.content, 'html.parser')
        words_l = soup.find_all(is_translated_word)
        for word_l in words_l:
            text = word_l.text
            result_l.append(re.sub(r'\s+', ' ', text))

        return result_l

    def trans(word_l: list[int]) -> str:
        result_l = ''
        for letter_l in word_l:
            result_l += letters[letter_l]

        return result_l

    def increment(word_l: list[int]) -> list[int]:
        done = False
        result_l = []
        for letter_l in word_l:
            if done:
                result_l.append(letter_l)
                continue
            next_letter_l = letter_l + 1
            if next_letter_l == letters_count:
                result_l.append(0)
                continue

            result_l.append(next_letter_l)
            done = True

        return result_l

    for length in range(longest_sensible_english_word_len - 1):
        length += 1
        combos = pow(length, letters_count)
        word = []
        for pos in range(length):
            word.append(0)
        for i in range(combos):
            result.append(get_words(trans(word)))
            word = increment(word)

    return result